In [1]:
import numpy as np;
import pandas as pd;
import plotly.express as px;
import json

## Initialize Parameters

In [38]:
# Global parameters
NO_OF_DAYS = 100
modelParameter = {}
modelParameter["pi"] = 0.02
modelParameter["tE"] = 3
modelParameter["tI"] = 6
modelParameter["cw"] = 15
modelParameter["ch"] = 5

modelParameter["eBC"] = 2/3
modelParameter["eLD"] = 1/3
modelParameter["eDB"] = 1/3
modelParameter["eHS"] = 1/4
modelParameter["eRZ"] = 1/3
modelParameter["eOZ"] = 1/2

modelParameter["aR"] = 0.1
modelParameter["dhsThreshold"] = 10
modelParameter["dzOZThreshold"] = 1
modelParameter["dzRZThreshold"] = 10

modelParameter["dhsOffsetDays"] = 7
modelParameter["dzOZOffsetDays"] = 21
modelParameter["dzRZOffsetDays"] = 7



district = "all"

print(modelParameter)


{'pi': 0.02, 'tE': 3, 'tI': 6, 'cw': 15, 'ch': 5, 'eBC': 0.6666666666666666, 'eLD': 0.3333333333333333, 'eDB': 0.3333333333333333, 'eHS': 0.25, 'eRZ': 0.3333333333333333, 'eOZ': 0.5, 'aR': 0.1, 'dhsThreshold': 10, 'dzOZThreshold': 1, 'dzRZThreshold': 10, 'dhsOffsetDays': 7, 'dzOZOffsetDays': 21, 'dzRZOffsetDays': 7}


## Load and Initialize Data

In [3]:
## Population data
initDataDF = pd.read_csv("../data/" + district + "_init_data.csv")
popDataDF = pd.read_csv("../data/" + district + "_population_data.csv")


cSparseMatrix = pd.read_csv("../output/" + district + "_cmatrix_results.csv")

## Number of regions
r = len(initDataDF.index)

## cijMatrix
C_TPart_Matrix = cSparseMatrix['Cij'].to_numpy().reshape(r,r)

## Sort distance data by name for easy matrix transformation
initDataDF.sort_values(by=['name'], inplace=True)
initDataDF.reset_index(drop=True, inplace=True)

popDataDF.sort_values(by=['name'], inplace=True)
popDataDF.reset_index(drop=True, inplace=True)


initDataDF['N'] = popDataDF['N']
initDataDF['type'] = popDataDF['type']
initDataDF['district'] = initDataDF['name'].str.split("__",n = 2, expand = True)[1] 

## Workplace matrix
Wn = modelParameter["cw"]*C_TPart_Matrix
Wn
Wn.sum(axis=1)[0:7]



array([15., 15., 15., 15., 15., 15., 15.])

## User parameters

In [4]:
#userParameter = '{ "breakTheChains" : [{"startDay": 7, "endDay": 120}], "completeLockDowns" :  [{"startDay": 14, "endDay": 35}], "districtLockDowns" :  [{"startDay": 36, "endDay": 50}], "hotSpots": [{"name":"Ajanur__Kasaragod", "startDay":51, "endDay":75}, {"name":"Kanjangad(M)__Kasaragod", "startDay":51, "endDay": 100}], "redZones": [ {"district":"Kasaragod", "startDay":101, "endDay":120}, {"district":"Alappuzha", "startDay":101, "endDay":120}], "orangeZones": [{"district": "Palakkad", "startDay":50, "endDay":150}] }'
#userParameter = '{ "breakTheChains":[], "completeLockDowns":[], "districtLockDowns" :  [{"startDay": 30, "endDay": 120}], "hotSpots": [{"name":"Ajanur__Kasaragod", "startDay":30, "endDay":120}, {"name":"Kuttichal__Thiruvananthapuram", "startDay":30, "endDay": 120}], "redZones": [ {"district":"Kasaragod", "startDay":30, "endDay":120}, {"district":"Kannur", "startDay":30, "endDay":120}], "orangeZones": [{"district": "Palakkad", "startDay":30, "endDay":120}] }'
#userParameter = '{ "breakTheChains" : [{"startDay": 5, "endDay": 100}], "completeLockDowns" :  [], "districtLockDowns" :  [{"startDay": 10, "endDay": 50}], "hotSpots": [{"name":"Neyyattinkara(M)__Thiruvananthapuram", "startDay":10, "endDay":24}, {"name":"Chathanoor__Kollam", "startDay":10, "endDay": 24}], "redZones": [ {"district":"Kasaragod", "startDay":10, "endDay":38}, {"district":"Kannur", "startDay":10, "endDay":38}, {"district":"Idukki", "startDay":10, "endDay":38}], "orangeZones": [{"district": "Kottayam", "startDay":10, "endDay":38}] }'
userParameter = '{ "breakTheChains" : [], "completeLockDowns" :  [], "districtLockDowns" :  [], "hotSpots": [], "redZones": [], "orangeZones": [], "dynamicHotSpots":[{"startDay":1, "endDay":100}], "dynamicZones":[{"startDay":1, "endDay":100}]}'
userParameterData = json.loads(userParameter)
userParameterData



{'breakTheChains': [],
 'completeLockDowns': [],
 'districtLockDowns': [],
 'hotSpots': [],
 'redZones': [],
 'orangeZones': [],
 'dynamicHotSpots': [{'startDay': 1, 'endDay': 100}],
 'dynamicZones': [{'startDay': 1, 'endDay': 100}]}

### Testing init Data

In [5]:
## Test Case 1. Monsoon wedding - Tvm
#seedLocation = "Thiruvananthapuram(C)__Thiruvananthapuram"
seedLocation = "Kozhikkode(C)__Kozhikode"
initDataDF.loc[initDataDF['name']==seedLocation,'I'] = 200
initDataDF[initDataDF['name']==seedLocation]

name       S  E    I  R       N type   district
417  Kozhikkode(C)__Kozhikode  608503  0  200  0  608503    C  Kozhikode

## Mitigation Strategy Initializations

### Functions

In [6]:
def isMitigationEnabled(day, strategyName):
    if strategyName in userParameterData:
        for strategy in userParameterData[strategyName]:
            if day >= strategy['startDay'] and day <= strategy['endDay']:
                return True
    return False

### 1. Normal Day

In [7]:
Mn = np.ones((r,r))
Mn

array([[1., 1., 1., ..., 1., 1., 1.],
       [1., 1., 1., ..., 1., 1., 1.],
       [1., 1., 1., ..., 1., 1., 1.],
       ...,
       [1., 1., 1., ..., 1., 1., 1.],
       [1., 1., 1., ..., 1., 1., 1.],
       [1., 1., 1., ..., 1., 1., 1.]])

### 2. Break the chain

In [8]:
Mbc = Mn*modelParameter["eBC"]
Mbc

array([[0.66666667, 0.66666667, 0.66666667, ..., 0.66666667, 0.66666667,
        0.66666667],
       [0.66666667, 0.66666667, 0.66666667, ..., 0.66666667, 0.66666667,
        0.66666667],
       [0.66666667, 0.66666667, 0.66666667, ..., 0.66666667, 0.66666667,
        0.66666667],
       ...,
       [0.66666667, 0.66666667, 0.66666667, ..., 0.66666667, 0.66666667,
        0.66666667],
       [0.66666667, 0.66666667, 0.66666667, ..., 0.66666667, 0.66666667,
        0.66666667],
       [0.66666667, 0.66666667, 0.66666667, ..., 0.66666667, 0.66666667,
        0.66666667]])

### 3. Complete Lockdown


In [9]:
Mld = Mn*modelParameter["eLD"]
Mld

array([[0.33333333, 0.33333333, 0.33333333, ..., 0.33333333, 0.33333333,
        0.33333333],
       [0.33333333, 0.33333333, 0.33333333, ..., 0.33333333, 0.33333333,
        0.33333333],
       [0.33333333, 0.33333333, 0.33333333, ..., 0.33333333, 0.33333333,
        0.33333333],
       ...,
       [0.33333333, 0.33333333, 0.33333333, ..., 0.33333333, 0.33333333,
        0.33333333],
       [0.33333333, 0.33333333, 0.33333333, ..., 0.33333333, 0.33333333,
        0.33333333],
       [0.33333333, 0.33333333, 0.33333333, ..., 0.33333333, 0.33333333,
        0.33333333]])

### 4. District Border Closure

In [10]:
cSparseMatrix['iNameDistrict'] = cSparseMatrix['iName'].str.split("__",n = 2, expand = True)[1] 
cSparseMatrix['jNameDistrict'] = cSparseMatrix['jName'].str.split("__", n = 2, expand = True)[1] 

cSparseMatrix.loc[cSparseMatrix['iNameDistrict']==cSparseMatrix['jNameDistrict'],'interDistrictFlag'] = 0
cSparseMatrix.loc[cSparseMatrix['iNameDistrict']!=cSparseMatrix['jNameDistrict'],'interDistrictFlag'] = 1



Mdb = cSparseMatrix['interDistrictFlag'].to_numpy().reshape(r,r)*modelParameter["eDB"]
Mdb[Mdb==0] = 1
Mdb



array([[1.        , 0.33333333, 0.33333333, ..., 1.        , 0.33333333,
        0.33333333],
       [0.33333333, 1.        , 0.33333333, ..., 0.33333333, 0.33333333,
        0.33333333],
       [0.33333333, 0.33333333, 1.        , ..., 0.33333333, 0.33333333,
        1.        ],
       ...,
       [1.        , 0.33333333, 0.33333333, ..., 1.        , 0.33333333,
        0.33333333],
       [0.33333333, 0.33333333, 0.33333333, ..., 0.33333333, 1.        ,
        0.33333333],
       [0.33333333, 0.33333333, 1.        , ..., 0.33333333, 0.33333333,
        1.        ]])

In [11]:
initDataDF.head(300).tail(30)
#Mdb[5,9]


name      S  E  I  R      N type  \
270                  Kallar__Kasaragod  19414  0  0  0  19414    P   
271         Kallara (Vaikom)__Kottayam  13562  0  0  0  13562    P   
272        Kallara__Thiruvananthapuram  25844  0  0  0  25844    P   
273      Kallikkad__Thiruvananthapuram  13553  0  0  0  13553    P   
274      Kalliyoor__Thiruvananthapuram  40816  0  0  0  40816    P   
275        Kallooppara__Pathanamthitta  16921  0  0  0  16921    P   
276             Kalloorkkad__Ernakulam  13337  0  0  0  13337    P   
277             Kalluvathukkal__Kollam  52541  0  0  0  52541    P   
278         Kalpakamcherri__Malappuram   6198  0  0  0   6198    P   
279               Kalpatta(M)__Wayanad  31580  0  0  0  31580    M   
280                 Kalyasseri__Kannur  31122  0  0  0  31122    P   
281                   Kamakshi__Idukki  19762  0  0  0  19762    P   
282                 Kanakari__Kottayam  22744  0  0  0  22744    P   
283                  Kanchiyar__Idukki  22513  0  0  0  22513    P   
284              Kandalloor__Alappuzha  19925  0  0  0  19925    P   
285             Kandanasseri__Thrissur  24452  0  0  0  24452    P   
286                 Kangazha__Kottayam  20115  0  0  0  20115    P   
287                   Kanichar__Kannur  19325  0  0  0  19325    P   
288              Kaniyampatta__Wayanad   7672  0  0  0   7672    P   
289            Kanjangad(M)__Kasaragod  73342  0  0  0  73342    M   
290             Kanjikkuzhi__Alappuzha  29951  0  0  0  29951    P   
291  Kanjiramkulam__Thiruvananthapuram  18821  0  0  0  18821    P   
292             Kanjirapally__Kottayam  43057  0  0  0  43057    P   
293            Kanjirappuzha__Palakkad  32999  0  0  0  32999    P   
294                 Kanjoor__Ernakulam  22541  0  0  0  22541    P   
295         Kankole Alapadamba__Kannur  15570  0  0  0  15570    P   
296                  Kannadi__Palakkad  24030  0  0  0  24030    P   
297          Kannamangalam__Malappuram   7194  0  0  0   7194    P   
298                Kannambra__Palakkad  25084  0  0  0  25084    P   
299                 Kannapuram__Kannur  18459  0  0  0  18459    P   

               district  
270           Kasaragod  
271            Kottayam  
272  Thiruvananthapuram  
273  Thiruvananthapuram  
274  Thiruvananthapuram  
275      Pathanamthitta  
276           Ernakulam  
277              Kollam  
278          Malappuram  
279             Wayanad  
280              Kannur  
281              Idukki  
282            Kottayam  
283              Idukki  
284           Alappuzha  
285            Thrissur  
286            Kottayam  
287              Kannur  
288             Wayanad  
289           Kasaragod  
290           Alappuzha  
291  Thiruvananthapuram  
292            Kottayam  
293            Palakkad  
294           Ernakulam  
295              Kannur  
296            Palakkad  
297          Malappuram  
298            Palakkad  
299              Kannur

### 5. Hot spots

In [12]:
def fillRegion(M, i, e):
    M[:,i] = e
    M[i,:] = e
    return M

In [13]:
def getHotSpotMitigationMatrix(day):
    M = np.ones((r,r))
    for hotSpot in userParameterData['hotSpots']:
        if day >= hotSpot['startDay'] and day <= hotSpot['endDay']:
            region = hotSpot['name']
            regionIndex = initDataDF.index[initDataDF['name'] == region][0]
            M = fillRegion(M, regionIndex, modelParameter["eHS"])
    return M


In [14]:
Mtest = getHotSpotMitigationMatrix(52)
Mtest[289,7]

1.0

### 6.Red and Orange Zones

In [15]:
def getRedZoneMitigationMatrix(day):
    M = np.ones((r,r))
    for redzones in userParameterData['redZones']:
        if day >= redzones['startDay'] and day <= redzones['endDay']:
            district = redzones['district']
            regionsInDistrictList = initDataDF.index[initDataDF['district'] == district]
            for regionsInDistrictIndex in regionsInDistrictList:
                fillRegion(M, regionsInDistrictIndex, modelParameter["eRZ"])
                
            
    return M


In [16]:
def getOrangeZoneMitigationMatrix(day):
    M = np.ones((r,r))
    for orangezones in userParameterData['orangeZones']:
        if day >= orangezones['startDay'] and day <= orangezones['endDay']:
            district = orangezones['district']
            regionsInDistrictList = initDataDF.index[initDataDF['district'] == district]
            for regionsInDistrictIndex in regionsInDistrictList:
                fillRegion(M, regionsInDistrictIndex, modelParameter["eOZ"])
                
            
    return M


In [17]:
Mtest = getRedZoneMitigationMatrix(103)
Mtest[456,7]

1.0

### 7. Dynamic Hot Spot

In [18]:
def updateDynamicHotSpots(day, IPrev):
    #print("day = ", day, "IPrev index", np.where(IPrev > 10))
    dynamicHotSpotsForDay = {}
    dynamicHotSpotsForDay["decisionDay"] = day
    dynamicHotSpotsForDay["regionIndices"] = np.where(IPrev*modelParameter["aR"] > modelParameter["dhsThreshold"])
    dynamicHotSpotsForDay["startDay"] = day
    dynamicHotSpotsForDay["endDay"] = day + modelParameter["dhsOffsetDays"]
    return dynamicHotSpotsForDay;

In [19]:
def getDynamicHotSpotMitigationMatrix(day, dynamicHotSpots):
    M = np.ones((r,r))
    for dynamicHotSpot in dynamicHotSpots:
        if day >= dynamicHotSpot['startDay'] and day <= dynamicHotSpot['endDay']:
            for regionIndex in dynamicHotSpot['regionIndices']:
                print("regionIndex:", regionIndex, " in hotpsot on day ", day)
                M = fillRegion(M, regionIndex, modelParameter["eHS"])
    return M


### 8. Dynamic Zones

In [20]:
def updateDynamicZones(day, IPrev, districts, dynamicZones):
    #print("day = ", day, "IPrev index", np.where(IPrev > 10))
    dynamicOrangeZoneForDay = {}
    dynamicOrangeZoneForDay["decisionDay"] = day
    dynamicOrangeZoneForDay["districts"] = []

    dynamicRedZoneForDay = {}
    dynamicRedZoneForDay["decisionDay"] = day
    dynamicRedZoneForDay["districts"] = []

    for district in districts:
        #print("processing district ", district)
        regionInDistrictIndices = initDataDF.index[initDataDF["district"] == district]
        #print("indices = " ,regionInDistrictIndices)
        districtISum = IPrev[regionInDistrictIndices].sum()
        #print("districtISum = " ,districtISum)
        ## Orange Zone
        if districtISum * modelParameter["aR"] > modelParameter["dzOZThreshold"] and districtISum * modelParameter["aR"] <= modelParameter["dzRZThreshold"]:
            ozDistricts = {}
            print(district, ' in Orange Zone on ', day)
            ozDistricts["district"] = district
            ozDistricts["startDay"] = day
            ozDistricts["endDay"] = day + modelParameter["dzOZOffsetDays"]
            dynamicOrangeZoneForDay["districts"].append(ozDistricts)
            dynamicZones["orangeZones"].append(dynamicOrangeZoneForDay)
            
        ## Red Zone
        if districtISum * modelParameter["aR"] > modelParameter["dzRZThreshold"]:
            rzDistricts = {}
            print(district, ' in Red Zone on ', day)
            rzDistricts["district"] = district
            rzDistricts["startDay"] = day
            rzDistricts["endDay"] = day + modelParameter["dzRZOffsetDays"]
            dynamicRedZoneForDay["districts"].append(rzDistricts)
            dynamicZones["redZones"].append(dynamicRedZoneForDay)
        

    #print(dynamicZones)
    return dynamicZones;

In [21]:
def getDynamicOrangeZoneMitigationMatrix(day,dynamicZones):
    M = np.ones((r,r))
    if 'orangeZones' in dynamicZones:
        for orangezone in dynamicZones['orangeZones']:
            if day == orangezone['decisionDay'] and 'startDay' in orangezone and day >= orangezone['startDay'] and day <= orangezone['endDay']:
                district = orangezone['district']
                regionsInDistrictList = initDataDF.index[initDataDF['district'] == district]
                for regionsInDistrictIndex in regionsInDistrictList:
                    fillRegion(M, regionsInDistrictIndex, modelParameter["eOZ"])
                
            
    return M


In [22]:
def getDynamicOrangeZoneMitigationMatrix(day, dynamicOrangeZones):
    M = np.ones((r,r))
    for dynamicOrangeZone in dynamicOrangeZones:
        if day >= dynamicOrangeZone['startDay'] and day <= dynamicOrangeZone['endDay']:
            district = dynamicOrangeZone['district']
            regionsInDistrictList = initDataDF.index[initDataDF['district'] == district]
            for regionsInDistrictIndex in regionsInDistrictList:
                fillRegion(M, regionsInDistrictIndex, modelParameter["eOZ"])
                
            
    return M


In [41]:
def getDynamicRedZoneMitigationMatrix(day, dynamicRedZones):
    M = np.ones((r,r))
    for dynamicRedZone in dynamicRedZones:
        if day >= dynamicRedZone['startDay'] and day <= dynamicRedZone['endDay']:
            district = dynamicRedZone['district']
            regionsInDistrictList = initDataDF.index[initDataDF['district'] == district]
            for regionsInDistrictIndex in regionsInDistrictList:
                fillRegion(M, regionsInDistrictIndex, modelParameter["eRZ"])
                
            
    return M


## Function definitions

In [23]:
## Differential equation
def deriv(y,contactInfected, modelParameter):
    Si, Ei, Ii, Ri = y
    dSdt = -modelParameter["pi"] * Si * contactInfected
    dEdt = (modelParameter["pi"] * Si * contactInfected) - (Ei/modelParameter["tE"])
    dIdt = (Ei/modelParameter["tE"]) -  (Ii/modelParameter["tI"])
    dRdt = (Ii/modelParameter["tI"])
    return dSdt, dEdt, dIdt, dRdt

In [24]:
def getMitigationMatrix(day, dynamicHotSpots, dynamicZones):    
    ## Effective mitigation matrix
    Meffective = Mn
    
    if isMitigationEnabled(day,"breakTheChains"):
        Meffective = np.minimum(Meffective, Mbc)
        
    if isMitigationEnabled(day,"completeLockDowns"):
        Meffective = np.minimum(Meffective, Mld)
    
    if isMitigationEnabled(day,"districtLockDowns"):
        Meffective = np.minimum(Meffective, Mdb)
    
    if isMitigationEnabled(day,"hotSpots"):
        Mhs = getHotSpotMitigationMatrix(day)
        Meffective = np.minimum(Meffective, Mhs)
    
    if isMitigationEnabled(day,"redZones"):
        Mrz = getRedZoneMitigationMatrix(day)
        Meffective = np.minimum(Meffective, Mrz)
    
    if isMitigationEnabled(day,"orangeZones"):
        Moz = getOrangeZoneMitigationMatrix(day)
        Meffective = np.minimum(Meffective, Moz)
    
    if isMitigationEnabled(day,"dynamicHotSpots"):
        Mdhs = getDynamicHotSpotMitigationMatrix(day, dynamicHotSpots)
        Meffective = np.minimum(Meffective, Mdhs)

    if isMitigationEnabled(day,"dynamicZones"):
        MdzOZ = getDynamicOrangeZoneMitigationMatrix(day, dynamicZones)
        Meffective = np.minimum(Meffective, MdzOZ)
        MdzRZ = getDynamicRedZoneMitigationMatrix(day, dynamicZones)
        Meffective = np.minimum(Meffective, MdzRZ)
    
        
    return Meffective


In [25]:
idxTest = [632,106,7,13,8,274]
Mtest = getMitigationMatrix(39,[],{})

print(Mtest[idxTest,:][:,idxTest])

initDataDF[initDataDF['name']=='Chathanoor__Kollam']

initDataDF.iloc[idxTest]


[[1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1.]
 [1. 1. 1. 1. 1. 1.]]


name      S  E  I  R      N type  \
632  Neyyattinkara(M)__Thiruvananthapuram  70850  0  0  0  70850    M   
106                    Chathanoor__Kollam  28585  0  0  0  28585    P   
7                       Ajanur__Kasaragod  49153  0  0  0  49153    P   
13                        Alakode__Kannur  34878  0  0  0  34878    P   
8                   Akalakunnam__Kottayam  19718  0  0  0  19718    P   
274         Kalliyoor__Thiruvananthapuram  40816  0  0  0  40816    P   

               district  
632  Thiruvananthapuram  
106              Kollam  
7             Kasaragod  
13               Kannur  
8              Kottayam  
274  Thiruvananthapuram

In [26]:
def computeContactMatrix(day, dynamicHotSpots, dynamicZones):    
    Meffective = getMitigationMatrix(day, dynamicHotSpots, dynamicZones)        
    Cmitigated = np.multiply(Meffective,Wn)    
    np.fill_diagonal(Cmitigated, Cmitigated.diagonal() + modelParameter["ch"])
    return Cmitigated
    


In [27]:
Ctest = computeContactMatrix(12,[],{})
Ctest.sum(axis=1)
Wn.sum(axis=1)[0:7]


array([15., 15., 15., 15., 15., 15., 15.])

In [28]:
## Find the contact ratio
def findContactWithInfected(Ci, I, N, day):
    c = Ci*I/N
    return c.sum()

In [29]:
## derive next count for SEIHR compartments
def derivNext(y, rates) :
    S,E,I,R = y
    dSdt, dEdt, dIdt, dRdt = rates
    S1 = S + dSdt
    E1 = E + dEdt
    I1 = I + dIdt
    R1 = R + dRdt

    return S1, E1, I1, R1


## Run the model for all regions

In [39]:
yPrevDict = {};
yNextDict = {};
data = []
IPrevArr = []
NArray = []
dynamicHotSpots = []
dynamicZones = {"orangeZones":[], "redZones": []}
districts = initDataDF['district'].unique()

for index, row in initDataDF.iterrows():
    yPrevDict[row['name']] = row['S'], row['E'], row['I'], row['R'] 
    IPrevArr.append(row['I'])
    NArray.append(row['S'] + row['E'] + row['I'] + row['R'])

IPrev = np.array(IPrevArr);
N = np.array(NArray);

for day in range(1,NO_OF_DAYS):
    INextArr = [];
    
    if isMitigationEnabled(day,"dynamicHotSpots"):
        dynamicHotSpots.append(updateDynamicHotSpots(day, IPrev));
    
    if isMitigationEnabled(day,"dynamicZones"):
        dynamicZones = updateDynamicZones(day, IPrev, districts, dynamicZones)

    C = computeContactMatrix(day,dynamicHotSpots,dynamicZones)

    for index, row in initDataDF.iterrows():
        name = row['name'];
        y = yPrevDict[name]; 
        # Contact matrix
        contactInfected = findContactWithInfected(C[index],IPrev, N, day);
        rates = deriv(y, contactInfected, modelParameter)
        yNext = derivNext(y, rates) 
        
        yNextDict[name] = yNext
        data.append({'name': name, 'day': day, 'S': yNext[0], 'E': yNext[1], 'I': yNext[2], 'R': yNext[3]})
        INextArr.append(yNext[2])
    
    yPrevDict = yNextDict
    IPrev = np.array(INextArr);

resultsDF = pd.DataFrame(data);



Kozhikode  in Red Zone on  1
regionIndex: [417]  in hotpsot on day  1
Kozhikode  in Red Zone on  2
regionIndex: [417]  in hotpsot on day  2
Kozhikode  in Red Zone on  3
regionIndex: [417]  in hotpsot on day  3
Kozhikode  in Red Zone on  4
regionIndex: [417]  in hotpsot on day  4
Kozhikode  in Red Zone on  5
regionIndex: [417]  in hotpsot on day  5
Kozhikode  in Red Zone on  6
regionIndex: [417]  in hotpsot on day  6
Kozhikode  in Red Zone on  7
regionIndex: [417]  in hotpsot on day  7
Kozhikode  in Red Zone on  8
regionIndex: [417]  in hotpsot on day  8
Kozhikode  in Red Zone on  9
regionIndex: [417]  in hotpsot on day  9
Kozhikode  in Red Zone on  10
regionIndex: [417]  in hotpsot on day  10
Kozhikode  in Red Zone on  11
regionIndex: [417]  in hotpsot on day  11
Kozhikode  in Red Zone on  12
regionIndex: [417]  in hotpsot on day  12
Kozhikode  in Red Zone on  13
regionIndex: [417]  in hotpsot on day  13
Kozhikode  in Red Zone on  14
regionIndex: [417]  in hotpsot on day  14
Kozhikode 

Malappuram  in Red Zone on  58
Thrissur  in Red Zone on  58
Kollam  in Orange Zone on  58
Idukki  in Orange Zone on  58
Palakkad  in Red Zone on  58
Ernakulam  in Orange Zone on  58
Kasaragod  in Orange Zone on  58
Kottayam  in Orange Zone on  58
Alappuzha  in Orange Zone on  58
Kannur  in Red Zone on  58
Wayanad  in Orange Zone on  58
Thiruvananthapuram  in Orange Zone on  58
Kozhikode  in Red Zone on  58
regionIndex: [417 646]  in hotpsot on day  58
Malappuram  in Red Zone on  59
Thrissur  in Red Zone on  59
Kollam  in Orange Zone on  59
Idukki  in Orange Zone on  59
Pathanamthitta  in Orange Zone on  59
Palakkad  in Red Zone on  59
Ernakulam  in Orange Zone on  59
Kasaragod  in Orange Zone on  59
Kottayam  in Orange Zone on  59
Alappuzha  in Orange Zone on  59
Kannur  in Red Zone on  59
Wayanad  in Orange Zone on  59
Thiruvananthapuram  in Orange Zone on  59
Kozhikode  in Red Zone on  59
regionIndex: [417 646]  in hotpsot on day  59
Malappuram  in Red Zone on  60
Thrissur  in Red Zo

Malappuram  in Red Zone on  75
Thrissur  in Red Zone on  75
Kollam  in Red Zone on  75
Idukki  in Red Zone on  75
Pathanamthitta  in Orange Zone on  75
Palakkad  in Red Zone on  75
Ernakulam  in Red Zone on  75
Kasaragod  in Red Zone on  75
Kottayam  in Red Zone on  75
Alappuzha  in Red Zone on  75
Kannur  in Red Zone on  75
Wayanad  in Red Zone on  75
Thiruvananthapuram  in Red Zone on  75
Kozhikode  in Red Zone on  75
regionIndex: [ 67  87 105 114 116 126 232 244 263 264 300 358 372 383 415 417 440 453
 471 481 504 535 562 601 608 646 648 685 703 730 745 754 765 813 821 849
 859 864 889 890 918 934 936 941]  in hotpsot on day  75
Malappuram  in Red Zone on  76
Thrissur  in Red Zone on  76
Kollam  in Red Zone on  76
Idukki  in Red Zone on  76
Pathanamthitta  in Orange Zone on  76
Palakkad  in Red Zone on  76
Ernakulam  in Red Zone on  76
Kasaragod  in Red Zone on  76
Kottayam  in Red Zone on  76
Alappuzha  in Red Zone on  76
Kannur  in Red Zone on  76
Wayanad  in Red Zone on  76
Thiru

Malappuram  in Red Zone on  87
Thrissur  in Red Zone on  87
Kollam  in Red Zone on  87
Idukki  in Red Zone on  87
Pathanamthitta  in Red Zone on  87
Palakkad  in Red Zone on  87
Ernakulam  in Red Zone on  87
Kasaragod  in Red Zone on  87
Kottayam  in Red Zone on  87
Alappuzha  in Red Zone on  87
Kannur  in Red Zone on  87
Wayanad  in Red Zone on  87
Thiruvananthapuram  in Red Zone on  87
Kozhikode  in Red Zone on  87
regionIndex: [  15   32   51   67   72   82   87   95  103  105  113  114  116  126
  135  140  147  177  211  232  233  244  263  264  279  300  302  307
  333  339  341  343  347  358  360  363  366  372  383  388  389  391
  400  411  413  415  417  440  441  446  448  453  463  471  476  481
  492  501  504  526  529  535  549  553  562  576  594  596  601  608
  609  633  640  646  648  649  651  665  671  685  698  703  728  730
  735  744  745  754  765  787  802  813  821  842  849  852  859  864
  875  882  889  890  893  894  895  899  918  924  934  936  941  94

Malappuram  in Red Zone on  95
Thrissur  in Red Zone on  95
Kollam  in Red Zone on  95
Idukki  in Red Zone on  95
Pathanamthitta  in Red Zone on  95
Palakkad  in Red Zone on  95
Ernakulam  in Red Zone on  95
Kasaragod  in Red Zone on  95
Kottayam  in Red Zone on  95
Alappuzha  in Red Zone on  95
Kannur  in Red Zone on  95
Wayanad  in Red Zone on  95
Thiruvananthapuram  in Red Zone on  95
Kozhikode  in Red Zone on  95
regionIndex: [   0    1    5    7    9   13   15   18   25   28   32   33   34   38
   41   44   47   50   51   52   67   72   79   81   82   87   95   97
   98   99  103  104  105  107  110  111  112  113  114  116  117  118
  122  123  126  135  136  137  140  144  147  153  158  160  162  163
  171  174  177  190  203  204  209  211  213  221  232  233  238  239
  244  248  250  253  255  261  262  263  264  279  280  285  287  288
  289  293  297  300  302  305  307  312  313  328  329  331  333  337
  339  341  343  347  350  351  358  360  363  366  368  371  372  37

Wayanad  in Red Zone on  99
Thiruvananthapuram  in Red Zone on  99
Kozhikode  in Red Zone on  99
regionIndex: [   0    1    5    7    9   11   13   15   18   19   22   25   28   32
   33   34   38   41   43   44   47   50   51   52   63   67   69   72
   75   79   81   82   84   85   87   88   95   97   98   99  100  103
  104  105  107  109  110  111  112  113  114  116  117  118  122  123
  126  133  135  136  137  140  142  144  146  147  148  153  158  160
  161  162  163  166  168  170  171  174  175  177  178  184  186  189
  190  194  203  204  209  210  211  212  213  218  219  221  224  228
  232  233  236  238  239  244  246  248  250  251  253  255  261  262
  263  264  267  269  278  279  280  285  287  288  289  293  296  297
  298  299  300  302  305  307  312  313  315  326  328  329  331  333
  337  338  339  341  343  344  346  347  348  350  351  352  355  357
  358  360  361  363  364  366  367  368  369  371  372  373  376  377
  378  379  381  382  383  384  387  3

In [ ]:
resultsDF.head(10)

## Save Output

In [ ]:
resultsDF.to_csv("../output/" + district + "_results.csv")

## Plot Results

In [40]:
plotsDF = resultsDF.copy()
plotsDF['TotalI'] = plotsDF['I']
plotsDF['day'] = plotsDF['day']
plotsDF['name'] = plotsDF['name']

plotsDF = plotsDF.drop(plotsDF[plotsDF['TotalI']==0].index,axis=0)

fig = px.scatter(plotsDF, x="day", y="TotalI", color="name")
fig.show()

In [ ]:
import plotly.graph_objects as go
figGo = go.Figure()

for index, row in initDataDF.iterrows(): 
    figGo.add_trace(go.Scatter(
    x=resultsDF[resultsDF['name']==row['name']]['day'],
    y=resultsDF[resultsDF['name']==row['name']]['I'],
    name=row['name']))


figGo.update_layout(yaxis_type="log")
figGo.show()

In [ ]:
idx = resultsDF.groupby(['name'])['I'].transform(max) == resultsDF['I']
resultsDF[idx].to_csv("../output/" + district + "_peak_results.csv")
resultsDF[idx]

In [35]:
idx = resultsDF['I'] > 500
resultsGT500DF = resultsDF[idx]
idxGTFirst = resultsGT500DF.groupby(['name'])['day'].transform(min) == resultsGT500DF['day']
resultsGT500FirstDF = resultsGT500DF[idxGTFirst]
idxGTFirstCorp = resultsGT500FirstDF['name'].str.contains('\(M\)|\(C\)',regex=True)
#idxGTFirstCorp = resultsGT500FirstDF['name'].str.contains('__Thiruvananthapuram',regex=True)

resultsGT500FirstDF[idxGTFirstCorp].head(50)
#resultsGT500DF

name  day              S  \
102882                   Kozhikkode(C)__Kozhikode  100  604504.277669   
109035                        Kochi(C)__Ernakulam  106  599900.874257   
109593                      Thrissur(C)__Thrissur  106  313781.751218   
110010                          Kannur(C)__Kannur  107  230148.898539   
112284                     Manjeri(M)__Malappuram  109   94867.501048   
112545                     Ponnani(M)__Malappuram  109   88179.910201   
112675  Thiruvananthapuram(C)__Thiruvananthapuram  109  964943.051308   
113194                          Kollam(C)__Kollam  110  386074.681674   
113198                    Kondotty(M)__Malappuram  110   57238.640797   
113230                    Koyilandi(M)__Kozhikode  110   69459.438314   
113296                  Malappuram(M)__Malappuram  110   65873.294553   
113480                      Palakkad(M)__Palakkad  110  128835.938727   
113518              Parappanangadi(M)__Malappuram  110   68457.245284   
113667                      Thalasseri(M)__Kannur  110   90274.830340   
113679                      Thanur(M)__Malappuram  110   67493.695572   
113704                      Thirur(M)__Malappuram  110   53691.005369   
113705                Thirurangadi(M)__Malappuram  110   54318.754936   
113756                     Vadakara(M)__Kozhikode  110   73102.733063   
113868                    Alappuzha(M)__Alappuzha  111  172374.600097   
114083                     Guruvayur(M)__Thrissur  111   67970.179928   
114250                   Kottakkal(M)__Malappuram  111   42131.600060   
114548                          Panoor(M)__Kannur  111   55664.068443   
114578                       Payyannur(M)__Kannur  111   70251.813816   
115117                       Feroke(M)__Kozhikode  112   51542.314097   
115123                 Iringalakkuda(M)__Thrissur  112   60629.469184   
115124                          Iritty(M)__Kannur  112   38474.373928   
115174                    Kanjangad(M)__Kasaragod  112   71435.714613   
115256                  Kodungalloor(M)__Thrissur  112   69442.158477   
115257                    Koduvalli(M)__Kozhikode  112   46264.304841   
115292                      Kottayam(M)__Kottayam  112  136447.209251   
115326                   Kunnamkulam(M)__Thrissur  112   52039.836095   
115377                   Mananthavady(M)__Wayanad  112   45799.540198   
115414                      Mattannoor(M)__Kannur  112   45153.175514   
115518                    Nilambur(M)__Malappuram  112   44066.986930   
115539                    Ottappalam(M)__Palakkad  112   51793.220532   
115615                      Payyoli(M)__Kozhikode  112   47193.033426   
115629              Perinthalmanna(M)__Malappuram  112   47606.192777   
115828                Vadakkancherri(M)__Thrissur  112   59346.025429   
115840                 Valancherri(M)__Malappuram  112   38157.638523   
116017                    Chalakkudi(M)__Thrissur  113   47659.451635   
116027                     Chavakkad(M)__Thrissur  113   37231.269126   
116057               Cherppulassery (M)__Palakkad  113   32914.804542   
116187                  Kalamasseri(M)__Ernakulam  113   69317.577500   
116199                       Kalpatta(M)__Wayanad  113   29347.648485   
116248                    Kasaragod(M)__Kasaragod  113   52204.729097   
116252                      Kattappana(M)__Idukki  113   50399.239700   
116482                       Mukkam(M)__Kozhikode  113   38273.677722   
116755                       Shornur(M)__Palakkad  113   41485.061848   
116758                  Sreekandapuram(M)__Kannur  113   31645.651307   
116762                Sulthan Bathery(M)__Wayanad  113   43223.864537   

                 E           I            R  
102882  295.750892  510.363393  3392.608047  
109035  589.097015  534.596797  1021.431931  
109593  548.630063  520.639404  1105.979315  
110010  561.050838  559.091635  1216.958987  
112284  473.223461  505.217881  1256.057610  
112545  536.987316  559.071996  1215.030488  

In [ ]:


mergeDataDF = initDataDF[["name","N","type","district"]]
resultsGT500DFMerge = pd.merge(resultsGT500DF[idxGTFirst],mergeDataDF,on="name",how="inner")

distanceData = pd.read_csv("../data/" + district + "_distance_matrix.csv")
distanceData.sort_values(by=['fromName', 'toName'], inplace=True)
distanceData.reset_index(drop=True, inplace=True)

distanceData['joinedName'] = distanceData['fromName'] + "-" + distanceData['toName']
iName = seedLocation
resultsGT500DFMerge['joinedName'] = iName + "-" + resultsGT500DFMerge['name']
resultsGT500DFMergeFinal = pd.merge(resultsGT500DFMerge, distanceData, on="joinedName", how="inner")
resultsGT500DFMergeFinal.head(20)